In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from pycaret.regression import *
from sklearn.impute import KNNImputer

In [3]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

# Data

In [8]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10   X_11   X_12  \
0     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
1     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
2     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
3     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
4     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
..    ...   ...  ...   ...   ...  ...   ...   ...   ...   ...    ...    ...   
593   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  468.9  473.9   
594   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
595   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
596  40.0  94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  505.8  510.9   
597  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  470.6  474.9   

      X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20   X_21   X_22  X_23  \
0      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...   ...   ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  459.2   0.0   0.0  247.5  248.0  247.3  250.0  527.0  538.0  522.0  0.19   
594    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  497.1   0.0   0.0  247.5  248.1  247.3  250.0  489.0  498.0  485.0  0.19   
597  462.9   0.0   0.0  247.5  248.0  247.3  250.0  525.0  534.0  520.0  0.19   

     X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31   X_32   X_33  \
0     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..    ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
594   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
597  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   

      X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  X_43  X_44  \
0      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN

In [5]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [9]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [10]:
train_data.drop(colls, inplace = True, axis = 1)

In [154]:
train_data = train_data.drop(['MONTH', 'MINUTE', 'DAY', 'YEAR'], axis = 1)

In [11]:
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10   X_11   X_12  \
0     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
1     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
2     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
3     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
4     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
..    ...   ...  ...   ...   ...  ...   ...   ...   ...   ...    ...    ...   
593   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  468.9  473.9   
594   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
595   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
596  40.0  94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  505.8  510.9   
597  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  470.6  474.9   

      X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20   X_21   X_22  X_23  \
0      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...   ...   ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  459.2   0.0   0.0  247.5  248.0  247.3  250.0  527.0  538.0  522.0  0.19   
594    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  497.1   0.0   0.0  247.5  248.1  247.3  250.0  489.0  498.0  485.0  0.19   
597  462.9   0.0   0.0  247.5  248.0  247.3  250.0  525.0  534.0  520.0  0.19   

     X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31   X_32   X_33  \
0     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..    ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
594   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
597  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   

      X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  X_43  X_44  \
0      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN

In [12]:
'''
train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7
'''
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [13]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [14]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [15]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == 78 :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [16]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == 42 :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [17]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == 59 :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [18]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == 70 :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [19]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == 175 :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [20]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == 174 :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [21]:
T050304 = T050304.fillna(0)
T050307 = T050307.fillna(0)
T010305 = T010305.fillna(0)
T010306 = T010306.fillna(0)
T100304 = T100304.fillna(0)
T100306 = T100306.fillna(0)

In [18]:
T050304 = T050304.fillna(T050304.mean())
T050307 = T050307.fillna(T050307.mean())
T010305 = T010305.fillna(T010305.mean())
T010306 = T010306.fillna(T010306.mean())
T100304 = T100304.fillna(T100304.mean())
T100306 = T100306.fillna(T100306.mean())

In [166]:
zero_one = (train_data[train_data['Y_Class'] == 1]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 0]['Y_Quality'].max())/2
one_two = (train_data[train_data['Y_Class'] == 2]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 1]['Y_Quality'].max())/2
print(zero_one, one_two)

0.5250761905000001 0.5348968255


# T050304

In [22]:
T050304_class = T050304['Y_Class']
T050304_target = T050304['Y_Quality']
T050304_data = T050304.drop(['Y_Class', 'Y_Quality'], axis = 1)
T050304_data

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
0               1   7813.0   7813.0   0.19    0.2   0.19    0.2  228.0  228.0   
2               1   7815.0   7815.0   0.19    0.2   0.19    0.2  228.0  228.0   
4               1   7817.0   7817.0   0.19    0.2   0.18    0.2  228.0  228.0   
6               1   7820.0   7820.0   0.19    0.2   0.19    0.2  228.0  228.0   
8               1   7822.0   7822.0   0.19    0.2   0.19    0.2  228.0  228.0   
..            ...      ...      ...    ...    ...    ...    ...    ...    ...   
581             1  11864.0  11864.0   0.19    0.2   0.19    0.2  230.0  230.0   
582             1  11898.0  11898.0   0.18    0.2   0.18    0.2  230.0  230.0   
583             1  11920.0  11920.0   0.19    0.2   0.19    0.2  230.0  230.0   
594             1  14810.0  14810.0   0.19    0.2   0.19    0.2  304.0  304.0   
595             1  14813.0  14813.0   0.19    0.2   0.19    0.2  304.0  304.0   

     X_138  X_139  X_140  X_141  X_142  X_143   X_144   X_145   X_146  X_147  \
0    225.0  582.9  587.1  567.3    0.0    0.0  249.96  249.99  247.46  250.0   
2    225.0  583.8  587.6  572.9    0.0    0.0  249.97  249.99  249.10  250.0   
4    225.0  583.2  587.3  565.9    0.0    0.0  249.96  249.99  246.46  250.0   
6    225.0  583.4  587.3  543.9    0.0    0.0  249.95  249.99  235.56  250.0   
8    225.0  583.3  587.2  571.9    0.0    0.0  249.97  249.99  248.96  250.0   
..     ...    ...    ...    ...    ...    ...     ...     ...     ...    ...   
581  230.0  584.0  588.7  558.2    0.0    0.0  249.96  249.99  241.22  250.0   
582  230.0  583.3  588.4  570.1    0.0    0.0  249.96  249.99  248.11  250.0   
583  230.0  583.5  588.3  555.9    0.0    0.0  249.97  249.99  240.71  250.0   
594  304.0  588.9  594.6  574.8    0.0    0.0  249.97  249.99  247.79  250.0   
595  304.0  588.8  594.6  570.8    0.0    0.0  249.96  249.99  245.61  250.0   

     X_148  X_149  X_150  X_151  X_152  X_153  X_154  X_155  X_156  X_157  \
0    428.0  435.0  426.0  179.9  180.0  179.9  180.0  215.0  215.0  214.9   
2    427.0  434.0  425.0  179.9  180.0  179.8  180.0  215.0  215.0  214.9   
4    428.0  434.0  426.0  180.0  180.0  179.8  180.0  215.0  215.1  215.0   
6    428.0  434.0  425.0  180.0  180.1  179.9  180.0  214.9  215.0  214.9   
8    428.0  434.0  426.0  180.0  180.0  179.9  180.0  215.0  215.0  214.9   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
581  427.0  434.0  424.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
582  428.0  437.0  425.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
583  428.0  435.0  425.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
594  424.0  431.0  420.0  179.9  180.0  179.9  180.0  215.0  215.0  214.9   
595  424.0  431.0  420.0  180.0  180.0  179.9  180.0  215.0  215.1  215.0   

     X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  X_167  \
0    215.0  214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   
2    215.0  215.0  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   
4    215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  209.9   
6    215.0  215.0  215.0  214.9  215.0  210.0  210.0  209.9  210.0  210.0   
8    215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
581  215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
582  215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
583  215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  209.9   
594  215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
595  215.0  214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   

     X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  X_177  \
0    210.0  209.9  210.0  205.0  205.0  204.9  205.0  204.9  205.0  204.9   
2    210.0  209.9  210.0  204.9  205.0  204.9  205.0  204.9  205.0 

In [23]:
#13
setup_rgs = setup(data = T050304_data, target=T050304_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [24]:
T050304_total_models = []

T050304_model_rf = create_model('rf', fold = 5)
T050304_total_models.append(T050304_model_rf)

T050304_model_gbr = create_model('gbr', fold = 5)
T050304_total_models.append(T050304_model_gbr)

T050304_model_et = create_model('et', fold = 5)
T050304_total_models.append(T050304_model_et)

T050304_model_catboost = create_model('catboost', fold = 5)
T050304_total_models.append(T050304_model_catboost)

T050304_model_xgb = create_model('xgboost', fold = 5)
T050304_total_models.append(T050304_model_xgb)

T050304_model_ada = create_model('ada', fold = 5)
T050304_total_models.append(T050304_model_ada)

T050304_model_lightgbm = create_model('lightgbm', fold = 5)
T050304_total_models.append(T050304_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [25]:
T050304_model_rf = tune_model(T050304_model_rf, fold=5, choose_better = True)

T050304_model_gbr = tune_model(T050304_model_gbr, fold=5, choose_better = True)

T050304_model_et = tune_model(T050304_model_et, fold=5, choose_better = True)

T050304_model_catboost = tune_model(T050304_model_catboost, fold=5, choose_better = True)

T050304_model_xgb = tune_model(T050304_model_xgb, fold=5, choose_better = True)

T050304_model_ada = tune_model(T050304_model_ada, fold=5, choose_better = True)

T050304_model_lightgbm = tune_model(T050304_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [26]:
T050304_tuned_models = [T050304_model_rf, T050304_model_gbr, T050304_model_et, T050304_model_catboost, T050304_model_xgb, T050304_model_ada, T050304_model_lightgbm]
T050304_tuned_models

[RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(learning_rate=0.15, max_depth=8, max_features='sqrt',
                           min_impurity_decrease=0.0001, min_samples_leaf=2,
                           min_samples_split=4, n_estimators=210,
                           random_state=414, subsample=0.6),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=0.5,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.2, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=7, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=90, n_jobs=-1,
              num_parallel_tree=1

In [27]:
for model in T050304_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.527207  
55  55.099998  66.489998     1.0   0.524022          0.527486  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.530269  
55  55.099998  66.489998     1.0   0.524022          0.527034  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.520378  
55  55.099998  66.489998     1.0   0.524022          0.522535  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.525092  
55  55.099998  66.489998     1.0   0.524022          0.526020  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.527662  
55  55.099998  66.489998     1.0   0.524022          0.529405  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.526501  
55  55.099998  66.489998     1.0   0.524022          0.527545  
56   0.000000   0.000000     1.0   

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1  14813.0  14813.0   0.19   0.20   0.19    0.2  304.0  304.0   
55             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
56             1  13618.0  13618.0   0.20   0.21   0.20    0.2  465.0  465.0   
57             1  21668.0  21668.0   0.20   0.21   0.20    0.2  700.0  700.0   
58             1  19056.0  19056.0   0.20   0.21   0.20    0.2  527.0  527.0   
59             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
60             1  26596.0  26596.0   0.20   0.21   0.20    0.2  874.0  874.0   
61             1  11920.0  11920.0   0.19   0.20   0.19    0.2  230.0  230.0   
62             1  22288.0  22288.0   0.20   0.21   0.20    0.2  717.0  717.0   
63             1  11743.0  11743.0   0.20   0.21   0.19    0.2  421.0  421.0   
64             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
65             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
66             1   9467.0   9467.0   0.19   0.20   0.19    0.2  192.0  192.0   
67             1  25153.0  25153.0   0.20   0.21   0.20    0.2  828.0  828.0   
68             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
69             1  25083.0  25083.0   0.20   0.21   0.20    0.2  827.0  827.0   
70             1   8949.0   8949.0   0.19   0.20   0.18    0.2  253.0  253.0   
71             1  11898.0  11898.0   0.18   0.20   0.18    0.2  230.0  230.0   
72             1  22546.0  22546.0   0.20   0.21   0.20    0.2  726.0  726.0   
73             1  23554.0  23554.0   0.20   0.21   0.20    0.2  773.0  773.0   
74             1  23376.0  23376.0   0.20   0.21   0.20    0.2  769.0  769.0   
75             1   5539.0   5539.0   0.19   0.20   0.19    0.2  162.0  162.0   
76             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
77             1  24875.0  24875.0   0.20   0.21   0.20    0.2  823.0  823.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
54  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   
55  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
56  465.0  ...  367.981140   353.0   0.000000   0.000000   0.000000   
57  700.0  ...  368.207550   352.0  53.389999  57.480000  56.380001   
58  524.0  ...  368.660370   352.0  57.750000  65.480003  52.270000   
59  550.0  ...  368.962952   353.0  56.119999  61.099998  50.220001   
60  875.0  ...  362.388885   343.0   0.000000   0.000000   0.000000   
61  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
62  718.0  ...  368.555542   353.0  56.709999  61.840000  40.599998   
63  421.0  ...  367.166656   352.0   0.000000   0.000000   0.000000   
64  458.0  ...  368.245270   352.0  54.759998  54.930000  59.680000   
65   32.0  ...  368.433960   353.0  53.490002  58.759998  42.220001   
66  192.0  ...  359.462952   342.0  55.740002  56.610001  40.509998   
67  828.0  ...  360.358490   342.0  50.230000  59.320000  40.599998   
68  192.0  ...  364.500000   350.0  53.810001  51.840000  59.369999   
69  827.0  ...  367.685181   352.0  57.000000  55.599998  40.080002   
70  250.0  ...  368.407410   352.0   0.000000   0.000000   0.000000   
71  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
72  726.0  ...  367.641510   353.0  55.700001  57.740002  49.830002   
73  773.0  ...  368.185181   352.0  54.630001  59.049999  40.770000   
74  769.0  ...  367.603760   352.0  54.680000  59.840000  59.220001   
75  162.0  ...  367.407410   354.0  54.660000  54.439999  42.389999   
76  191.0  ...  370.528290   352.0  52.650002  58.950001  41.009998   
77  823.0  ...  358.792450   342.0  54.650002  62.369999  51.430000   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
54   0.000000   0.000000     1.0   0.521289          0.527876  
55  55.099998  66.489998     1.0   0.524022          0.527876  
56   0.000000   0.000000     1.0   

In [28]:
T050304_final_regression_model = finalize_model(T050304_model_xgb)

In [29]:
T050304_prediction = predict_model(T050304_final_regression_model, data=T050304_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [175]:
T050304_y_class = pd.DataFrame(T050304_class, columns = ['Y_Class'])
T050304_idx = T050304_y_class.index
T050304_y_class = T050304_y_class.reset_index()
T050304_prediction = pd.concat([T050304_prediction, T050304_y_class], axis = 1)
T050304_prediction = T050304_prediction.set_index('index')
T050304_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [176]:
#(train_data[train_data['Y_Class'] == 0]['Y_Quality'].min() <= T050304_prediction.iloc[i]['prediction_label']) and 
# and (T050304_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [38]:
T050304_prediction['Y_Class'] = 22

idx = T050304_prediction.index
for i in range (len(T050304_prediction)) :
    if (T050304_prediction.iloc[i]['prediction_label'] <= (0.525045+0.525095)/2) :
        T050304_prediction.loc[idx[i], 'Y_Class'] = 0
    elif ((0.525045+0.525095)/2 < T050304_prediction.iloc[i]['prediction_label']) and (T050304_prediction.iloc[i]['prediction_label'] < (0.534054+0.535405)/2) :
        T050304_prediction.loc[idx[i], 'Y_Class'] = 1
    elif ((0.534054+0.535405)/2 <= T050304_prediction.iloc[i]['prediction_label']) :
        T050304_prediction.loc[idx[i], 'Y_Class'] = 2
T050304_prediction

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
0              1   7813.0   7813.0   0.19    0.2   0.19    0.2  228.0  228.0   
1              1   7815.0   7815.0   0.19    0.2   0.19    0.2  228.0  228.0   
2              1   7817.0   7817.0   0.19    0.2   0.18    0.2  228.0  228.0   
3              1   7820.0   7820.0   0.19    0.2   0.19    0.2  228.0  228.0   
4              1   7822.0   7822.0   0.19    0.2   0.19    0.2  228.0  228.0   
..           ...      ...      ...    ...    ...    ...    ...    ...    ...   
73             1  11864.0  11864.0   0.19    0.2   0.19    0.2  230.0  230.0   
74             1  11898.0  11898.0   0.18    0.2   0.18    0.2  230.0  230.0   
75             1  11920.0  11920.0   0.19    0.2   0.19    0.2  230.0  230.0   
76             1  14810.0  14810.0   0.19    0.2   0.19    0.2  304.0  304.0   
77             1  14813.0  14813.0   0.19    0.2   0.19    0.2  304.0  304.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
0   225.0  ...  368.296295   353.0  39.340000  40.889999  32.560001   
1   225.0  ...  367.320740   353.0  39.189999  36.650002  42.470001   
2   225.0  ...  367.351837   352.0  38.700001  41.889999  46.930000   
3   225.0  ...  368.425934   353.0  32.500000  41.419998  38.360001   
4   225.0  ...  373.500000   353.0  42.250000  43.169998  55.599998   
..    ...  ...         ...     ...        ...        ...        ...   
73  230.0  ...  367.333344   352.0   0.000000   0.000000   0.000000   
74  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
75  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
76  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
77  304.0  ...  367.018860   352.0   0.000000   0.000000   0.000000   

       X_2869     X_2870  X_2871  prediction_label  Y_Class  
0   34.090000  77.769997     0.0          0.533013        1  
1   36.529999  78.349998     0.0          0.531610        1  
2   33.090000  76.970001     0.0          0.531531        1  
3   30.830000  76.930000     0.0          0.533627        1  
4   33.259998  78.500000     0.0          0.531873        1  
..        ...        ...     ...               ...      ...  
73   0.000000   0.000000     1.0          0.523482        0  
74  56.279999  66.830002     1.0          0.522485        0  
75  57.049999  63.180000     1.0          0.522577        0  
76  55.099998  66.489998     1.0          0.524285        0  
77   0.000000   0.000000     1.0          0.521349        0  

[78 rows x 1971 columns]

In [39]:
T050304_prediction['Y_Class'].unique()

array([1, 2, 0], dtype=int64)

# T050307

In [30]:
T050307_class = T050307['Y_Class']
T050307_target = T050307['Y_Quality']
T050307_data = T050307.drop(['Y_Class', 'Y_Quality'], axis = 1)
T050307_data

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
1               1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
3               1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
5               1  19859.0  19859.0   0.20   0.21   0.20    0.2  414.0  414.0   
7               1  19861.0  19861.0   0.20   0.21   0.20    0.2  414.0  414.0   
9               1  19864.0  19864.0   0.20   0.21   0.20    0.2  414.0  414.0   
11              1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
13              1  19869.0  19869.0   0.20   0.21   0.20    0.2  414.0  414.0   
15              1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
17              1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
19              1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
24              1  22589.0  22589.0   0.20   0.21   0.20    0.2  504.0  499.0   
35              1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
81              1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   
82              1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
187             1  19631.0  19631.0   0.20   0.21   0.19    0.2  609.0  609.0   
195             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
198             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
256             1  25395.0  25395.0   0.20   0.21   0.20    0.2  760.0  760.0   
261             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
296             1   1055.0   1055.0   0.20   0.21   0.20    0.2   50.0   52.0   
298             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
307             1   1232.0   1232.0   0.20   0.21   0.20    0.2   58.0   59.0   
316             1   1561.0   1561.0   0.20   0.21   0.20    0.2   67.0   69.0   
336             1   2705.0   2705.0   0.20   0.21   0.20    0.2  119.0  121.0   
355             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
356             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
369             1   4446.0   4446.0   0.20   0.21   0.20    0.2  178.0  180.0   
432             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
444             1  11538.0  11538.0   0.20   0.21   0.20    0.2  376.0  378.0   
454             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
477             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
541             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
542             1    829.0    829.0   0.19   0.20   0.19    0.2   58.0   58.0   
543             1    851.0    851.0   0.19   0.21   0.19    0.2   59.0   59.0   
544             1    874.0    874.0   0.19   0.21   0.19    0.2   59.0   59.0   
545             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
546             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
549             1   2248.0   2248.0   0.19   0.20   0.19    0.2   81.0   81.0   
550             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
551             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
552             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
555             1   2540.0   2540.0   0.19   0.20   0.19    0.2   87.0   87.0   

     X_138  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
1    414.0  ...   185.6   383.0  367.735849   353.0   38.89   42.82   43.92   
3    414.0  ...   165.8   384.0  369.188679   353.0   37.74   39.17   52.17   
5    414.0  ...   184.7   384.0  368.622641   352.0   38.16   51.25   56.01   
7    414.0  ...   173.8   393.0  370.283019   353.0   39.00   35.95   59.51   
9    414.0  ...   167.2   393.0  372.870370   353.0   34.40   35.88   50.36   
11   414.0  ...   166.1   394.0  374.425926   3

In [31]:
#13
setup_rgs = setup(data = T050307_data, target=T050307_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [32]:
T050307_total_models = []

T050307_model_rf = create_model('rf', fold = 5)
T050307_total_models.append(T050307_model_rf)

T050307_model_gbr = create_model('gbr', fold = 5)
T050307_total_models.append(T050307_model_gbr)

T050307_model_ada = create_model('ada', fold = 5)
T050307_total_models.append(T050307_model_ada)

T050307_model_catboost = create_model('catboost', fold = 5)
T050307_total_models.append(T050307_model_catboost)

T050307_model_xgb = create_model('xgboost', fold = 5)
T050307_total_models.append(T050307_model_xgb)

T050307_model_et = create_model('et', fold = 5)
T050307_total_models.append(T050307_model_et)

T050307_model_lightgbm = create_model('lightgbm', fold = 5)
T050307_total_models.append(T050307_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [33]:
T050307_model_rf = tune_model(T050307_model_rf, fold=5, choose_better = True)

T050307_model_gbr = tune_model(T050307_model_gbr, fold=5, choose_better = True)

T050307_model_ada = tune_model(T050307_model_ada, fold=5, choose_better = True)

T050307_model_catboost = tune_model(T050307_model_catboost, fold=5, choose_better = True)

T050307_model_xgb = tune_model(T050307_model_xgb, fold=5, choose_better = True)

T050307_model_et = tune_model(T050307_model_et, fold=5, choose_better = True)

T050307_model_lightgbm = tune_model(T050307_model_lightgbm, fold=5, choose_better = True)


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [34]:
T050307_tuned_models = [T050307_model_rf, T050307_model_gbr, T050307_model_ada, T050307_model_catboost, T050307_model_xgb, T050307_model_et, T050307_model_lightgbm]
T050307_tuned_models

[RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(learning_rate=0.15, max_depth=8, max_features='sqrt',
                           min_impurity_decrease=0.0001, min_samples_leaf=2,
                           min_samples_split=4, n_estimators=210,
                           random_state=414, subsample=0.6),
 AdaBoostRegressor(learning_rate=0.0005, n_estimators=140, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=0.5,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.4, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=8, max_leaves=0, min_child_weight=3,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_

In [35]:
for model in T050307_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.531884  
30  58.889999  65.269997     1.0   0.542848          0.545913  
31  58.790001  63.259998     1.0   0.521494          0.522709  
32   0.000000   0.000000     1.0   0.527976          0.545640  
33  35.340000  72.550003     0.0   0.541819          0.543725  
34   0.000000   0.000000     1.0   0.551949          0.540241  
35  57.009998  65.669998     1.0   0.524781          0.538558  
36  56.590000  66.830002     1.0   0.533695          0.532811  
37  58.959999  64.010002     1.0   0.525086          0.540381  
38  35.169998  71.400002     0.0   0.538854          0.540498  
39   0.000000   0.000000     1.0   0.547481          0.542647  
40   0.000000   0.000000     0.0   0.539235          0.541295  
41  57.169998  64.010002     1.0   0.544584          0.546032  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.533922  
30  58.889999  65.269997     1.0   0.542848          0.544292  
31  58.790001  63.259998     1.0   0.521494          0.527746  
32   0.000000   0.000000     1.0   0.527976          0.545012  
33  35.340000  72.550003     0.0   0.541819          0.545800  
34   0.000000   0.000000     1.0   0.551949          0.543611  
35  57.009998  65.669998     1.0   0.524781          0.535031  
36  56.590000  66.830002     1.0   0.533695          0.539289  
37  58.959999  64.010002     1.0   0.525086          0.532202  
38  35.169998  71.400002     0.0   0.538854          0.537339  
39   0.000000   0.000000     1.0   0.547481          0.535057  
40   0.000000   0.000000     0.0   0.539235          0.537339  
41  57.169998  64.010002     1.0   0.544584          0.539387  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.529496  
30  58.889999  65.269997     1.0   0.542848          0.539685  
31  58.790001  63.259998     1.0   0.521494          0.522131  
32   0.000000   0.000000     1.0   0.527976          0.538667  
33  35.340000  72.550003     0.0   0.541819          0.538860  
34   0.000000   0.000000     1.0   0.551949          0.539540  
35  57.009998  65.669998     1.0   0.524781          0.536801  
36  56.590000  66.830002     1.0   0.533695          0.530093  
37  58.959999  64.010002     1.0   0.525086          0.537720  
38  35.169998  71.400002     0.0   0.538854          0.538701  
39   0.000000   0.000000     1.0   0.547481          0.539198  
40   0.000000   0.000000     0.0   0.539235          0.538832  
41  57.169998  64.010002     1.0   0.544584          0.539012  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.531688  
30  58.889999  65.269997     1.0   0.542848          0.547125  
31  58.790001  63.259998     1.0   0.521494          0.521021  
32   0.000000   0.000000     1.0   0.527976          0.541941  
33  35.340000  72.550003     0.0   0.541819          0.540706  
34   0.000000   0.000000     1.0   0.551949          0.545160  
35  57.009998  65.669998     1.0   0.524781          0.531317  
36  56.590000  66.830002     1.0   0.533695          0.533401  
37  58.959999  64.010002     1.0   0.525086          0.532950  
38  35.169998  71.400002     0.0   0.538854          0.538191  
39   0.000000   0.000000     1.0   0.547481          0.543887  
40   0.000000   0.000000     0.0   0.539235          0.537405  
41  57.169998  64.010002     1.0   0.544584          0.541376  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.543358  
30  58.889999  65.269997     1.0   0.542848          0.546517  
31  58.790001  63.259998     1.0   0.521494          0.523983  
32   0.000000   0.000000     1.0   0.527976          0.546016  
33  35.340000  72.550003     0.0   0.541819          0.547383  
34   0.000000   0.000000     1.0   0.551949          0.549658  
35  57.009998  65.669998     1.0   0.524781          0.530628  
36  56.590000  66.830002     1.0   0.533695          0.536581  
37  58.959999  64.010002     1.0   0.525086          0.542160  
38  35.169998  71.400002     0.0   0.538854          0.541200  
39   0.000000   0.000000     1.0   0.547481          0.554779  
40   0.000000   0.000000     0.0   0.539235          0.537755  
41  57.169998  64.010002     1.0   0.544584          0.543491  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.530824  
30  58.889999  65.269997     1.0   0.542848          0.544870  
31  58.790001  63.259998     1.0   0.521494          0.520791  
32   0.000000   0.000000     1.0   0.527976          0.544909  
33  35.340000  72.550003     0.0   0.541819          0.544220  
34   0.000000   0.000000     1.0   0.551949          0.546010  
35  57.009998  65.669998     1.0   0.524781          0.535527  
36  56.590000  66.830002     1.0   0.533695          0.534547  
37  58.959999  64.010002     1.0   0.525086          0.535932  
38  35.169998  71.400002     0.0   0.538854          0.539061  
39   0.000000   0.000000     1.0   0.547481          0.544407  
40   0.000000   0.000000     0.0   0.539235          0.542432  
41  57.169998  64.010002     1.0   0.544584          0.543172  

[13 rows x 1978 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
30             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
31             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
33             1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
34             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
35             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
36             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
37             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
38             1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
39             1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
40             1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
29   84.0  ...  369.433960   352.0  52.279999  56.240002  54.470001   
30  646.0  ...  369.092590   353.0  53.270000  56.009998  59.470001   
31   59.0  ...  368.905670   352.0  55.250000  51.049999  49.830002   
32  618.0  ...  368.509430   353.0   0.000000   0.000000   0.000000   
33  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
34  159.0  ...  366.867920   352.0   0.000000   0.000000   0.000000   
35  451.0  ...  367.283020   353.0  54.950001  56.810001  42.610001   
36   82.0  ...  363.037048   342.0  52.610001  53.099998  57.299999   
37  396.0  ...  367.074066   352.0  55.689999  53.029999  53.750000   
38  414.0  ...  369.169800   353.0  33.160000  33.259998  55.970001   
39  172.0  ...  367.679260   352.0   0.000000   0.000000   0.000000   
40  414.0  ...  369.037750   353.0   0.000000   0.000000   0.000000   
41  171.0  ...  369.358490   353.0  59.380001  57.130001  50.150002   

       X_2869     X_2870  X_2871  Y_Quality  prediction_label  
29  50.560001  62.529999     1.0   0.525271          0.535722  
30  58.889999  65.269997     1.0   0.542848          0.535722  
31  58.790001  63.259998     1.0   0.521494          0.535722  
32   0.000000   0.000000     1.0   0.527976          0.535722  
33  35.340000  72.550003     0.0   0.541819          0.535722  
34   0.000000   0.000000     1.0   0.551949          0.535722  
35  57.009998  65.669998     1.0   0.524781          0.535722  
36  56.590000  66.830002     1.0   0.533695          0.535722  
37  58.959999  64.010002     1.0   0.525086          0.535722  
38  35.169998  71.400002     0.0   0.538854          0.535722  
39   0.000000   0.000000     1.0   0.547481          0.535722  
40   0.000000   0.000000     0.0   0.539235          0.535722  
41  57.169998  64.010002     1.0   0.544584          0.535722  

[13 rows x 1978 columns]

In [36]:
T050307_final_regression_model = finalize_model(T050307_model_catboost)

In [37]:
#최종 예측
#29
T050307_prediction = predict_model(T050307_final_regression_model, data=T050307_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [40]:
T050307_y_class = pd.DataFrame(T050307_class, columns = ['Y_Class'])
T050307_idx = T050307_y_class.index
T050307_y_class = T050307_y_class.reset_index()
T050307_prediction = pd.concat([T050307_prediction, T050307_y_class], axis = 1)
T050307_prediction = T050307_prediction.set_index('index')
T050307_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [41]:
#(train_data[train_data['Y_Class'] == 0]['Y_Quality'].min() <= T050307_prediction.iloc[i]['prediction_label']) and 
# and (T050307_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [42]:
T050307_prediction['Y_Class'] = 22

T050307_idx = T050307_prediction.index
for i in range (len(T050307_prediction)) :
    if (T050307_prediction.iloc[i]['prediction_label'] <= (0.524781+0.525086)/2) :
        T050307_prediction.loc[T050307_idx[i], 'Y_Class'] = 0
    elif ((0.524781+0.525086)/2 < T050307_prediction.iloc[i]['prediction_label']) and (T050307_prediction.iloc[i]['prediction_label'] < (0.534843+0.537325)/2) :
        T050307_prediction.loc[T050307_idx[i], 'Y_Class'] = 1
    elif ((0.534843+0.537325)/2 <= T050307_prediction.iloc[i]['prediction_label']) :
        T050307_prediction.loc[T050307_idx[i], 'Y_Class'] = 2
T050307_prediction

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  \
index                                                                      
1                 1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0   
3                 1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0   
5                 1  19859.0  19859.0   0.20   0.21   0.20    0.2  414.0   
7                 1  19861.0  19861.0   0.20   0.21   0.20    0.2  414.0   
9                 1  19864.0  19864.0   0.20   0.21   0.20    0.2  414.0   
11                1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0   
13                1  19869.0  19869.0   0.20   0.21   0.20    0.2  414.0   
15                1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0   
17                1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0   
19                1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0   
24                1  22589.0  22589.0   0.20   0.21   0.20    0.2  504.0   
35                1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0   
81                1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0   
82                1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0   
187               1  19631.0  19631.0   0.20   0.21   0.19    0.2  609.0   
195               1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0   
198               1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0   
256               1  25395.0  25395.0   0.20   0.21   0.20    0.2  760.0   
261               1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0   
296               1   1055.0   1055.0   0.20   0.21   0.20    0.2   50.0   
298               1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   
307               1   1232.0   1232.0   0.20   0.21   0.20    0.2   58.0   
316               1   1561.0   1561.0   0.20   0.21   0.20    0.2   67.0   
336               1   2705.0   2705.0   0.20   0.21   0.20    0.2  119.0   
355               1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0   
356               1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0   
369               1   4446.0   4446.0   0.20   0.21   0.20    0.2  178.0   
432               1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0   
444               1  11538.0  11538.0   0.20   0.21   0.20    0.2  376.0   
454               1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0   
477               1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0   
541               1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   
542               1    829.0    829.0   0.19   0.20   0.19    0.2   58.0   
543               1    851.0    851.0   0.19   0.21   0.19    0.2   59.0   
544               1    874.0    874.0   0.19   0.21   0.19    0.2   59.0   
545               1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   
546               1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   
549               1   2248.0   2248.0   0.19   0.20   0.19    0.2   81.0   
550               1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   
551               1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   
552               1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   
555               1   2540.0   2540.0   0.19   0.20   0.19    0.2   87.0   

       X_137  X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
index                ...                                                        
1      414.0  414.0  ...  367.735840   353.0  38.889999  42.820000  43.919998   
3      414.0  414.0  ...  369.188690   353.0  37.740002  39.169998  52.169998   
5      414.0  414.0  ...  368.622650   352.0  38.160000  51.250000  56.009998   
7      414.0  414.0  ...  370.283020   353.0  39.000000  35.950001  59.509998   
9      414.0  414.0  ...  372.870361   353.0  34.400002  35.880001  50.360001   
11     414.0  414.0  ...  374.425934   352.0  39.160000  35.490002  52.270000   
13     414.0  

In [43]:
T050307_prediction['Y_Class'].unique()

array([2, 1, 0], dtype=int64)

# T010305

In [44]:
T010305_class = T010305['Y_Class']
T010305_target = T010305['Y_Quality']
T010305_data = T010305.drop(['Y_Class', 'Y_Quality'], axis = 1)
T010305_data

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
28              1    1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   
33              1    1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   
39              1    1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   
40              1    1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   
41              1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   
48              1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
52              1    2.0   87.0    0.0   45.0   11.0  114.0   45.0   11.0   
57              1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
58              1    1.0   88.0    0.0   45.0   11.0  119.0   45.0   11.0   
59              1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
64              1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
65              1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
66              1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
69              1    2.0   91.0    0.0   45.0   11.0  129.0   45.0   11.0   
71              1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
75              1    2.0   89.0    0.0   45.0   11.0  135.0   45.0   11.0   
77              1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
84              1    1.0   95.0    0.0   45.0   11.0  155.0   45.0   11.0   
90              1    2.0   89.0    0.0   45.0   11.0  163.0   45.0   11.0   
94              1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
95              1    2.0   90.0    0.0   45.0   11.0  168.0   45.0   11.0   
116             1    1.0   95.0    0.0   45.0   11.0    2.0   45.0   11.0   
118             1    1.0   91.0    0.0   45.0   11.0    2.0   45.0   12.0   
123             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
129             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
179             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
190             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
208             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   
220             1    2.0   93.0    0.0   45.0   11.0   34.0   45.0   11.0   
230             1    2.0   91.0    0.0   45.0   11.0   38.0   45.0   11.0   
235             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
239             1    2.0   88.0    0.0   45.0   11.0   44.0   45.0   11.0   
244             1    1.0   90.0    0.0   45.0   11.0   46.0   45.0   11.0   
281             1    2.0   88.0    0.0   45.0   11.0   85.0   45.0   11.0   
283             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
287             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
291             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
292             1    1.0   89.0    0.0   45.0   11.0   89.0   45.0   11.0   
295             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
299             1    1.0   96.0    0.0   45.0   11.0   93.0   45.0   11.0   
300             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
312             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
332             1    1.0   90.0    0.0   45.0   11.0  111.0   45.0   11.0   
334             1    2.0   88.0    0.0   45.0   11.0  111.0   45.0   11.0   
404             1    1.0   90.0    0.0   45.0   11.0   14.0   45.0   11.0   
410             1    1.0   88.0    0.0   45.0   11.0   19.0   45.0   11.0   
436             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
449             1   11.0   90.0    0.0   45.0   11.0   43.0   45.0   11.0   
455             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
456             1    1.0   91.0    0.0   45.0   11.0   45.0   45.0   11.0   
480             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
4

In [45]:
#13
setup_rgs = setup(data = T010305_data, target=T010305_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [46]:
T010305_total_models = []

T010305_model_rf = create_model('rf', fold = 5)
T010305_total_models.append(T010305_model_rf)

T010305_model_gbr = create_model('gbr', fold = 5)
T010305_total_models.append(T010305_model_gbr)

T010305_model_et = create_model('et', fold = 5)
T010305_total_models.append(T010305_model_et)

T010305_model_catboost = create_model('catboost', fold = 5)
T010305_total_models.append(T010305_model_catboost)

T010305_model_xgb = create_model('xgboost', fold = 5)
T010305_total_models.append(T010305_model_xgb)

T010305_model_ada = create_model('ada', fold = 5)
T010305_total_models.append(T010305_model_ada)

T010305_model_lightgbm = create_model('lightgbm', fold = 5)
T010305_total_models.append(T010305_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [47]:
T010305_model_rf = tune_model(T010305_model_rf, fold=5, choose_better = True)

T010305_model_gbr = tune_model(T010305_model_gbr, fold=5, choose_better = True)

T010305_model_et = tune_model(T010305_model_et, fold=5, choose_better = True)

T010305_model_catboost = tune_model(T010305_model_catboost, fold=5, choose_better = True)

T010305_model_xgb = tune_model(T010305_model_xgb, fold=5, choose_better = True)

T010305_model_ada = tune_model(T010305_model_ada, fold=5, choose_better = True)

T010305_model_lightgbm = tune_model(T010305_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [48]:
T010305_tuned_models = [T010305_model_rf, T010305_model_gbr, T010305_model_et, T010305_model_catboost, T010305_model_xgb, T010305_model_ada, T010305_model_lightgbm]
T010305_tuned_models

[RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(random_state=414),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
              reg_alpha=0, reg_lambda=1, ...),
 AdaBoostRegressor(learning_rate=0.3, n_estimators=40, random_state=414),
 LGBMRegressor(random_state=414)]

In [49]:
for model in T010305_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.528659  
42   466.0  447.942322   423.0   0.523173          0.529915  
43   466.0  445.075470   422.0   0.531036          0.534528  
44   466.0  448.442322   433.0   0.528190          0.529221  
45   466.0  443.923065   423.0   0.526241          0.527594  
46   466.0  447.750000   432.0   0.518024          0.527345  
47   466.0  447.961548   432.0   0.534486          0.532042  
48   456.0  438.596161   422.0   0.530303          0.529630  
49   456.0  439.924530   423.0   0.532754          0.529627  
50   466.0  444.924530   424.0   0.524686          0.530807  
51   466.0  442.150940   423.0   0.538614          0.533123  
52   466.0  447.923065   433.0   0.526741          0.528668  
53   436.0  419.134613   403.0   0.536859          0.532665  
54   456.0  439.480774   422.0   0.537116          0.533576  
55   463.0  440.867920   423.0   0.527910          0.532546  
56   466.0  449.192322   432.0   0.528856          0.526643  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.528064  
42   466.0  447.942322   423.0   0.523173          0.529901  
43   466.0  445.075470   422.0   0.531036          0.533814  
44   466.0  448.442322   433.0   0.528190          0.525888  
45   466.0  443.923065   423.0   0.526241          0.528221  
46   466.0  447.750000   432.0   0.518024          0.525601  
47   466.0  447.961548   432.0   0.534486          0.533880  
48   456.0  438.596161   422.0   0.530303          0.529193  
49   456.0  439.924530   423.0   0.532754          0.527338  
50   466.0  444.924530   424.0   0.524686          0.532959  
51   466.0  442.150940   423.0   0.538614          0.532573  
52   466.0  447.923065   433.0   0.526741          0.526792  
53   436.0  419.134613   403.0   0.536859          0.534063  
54   456.0  439.480774   422.0   0.537116          0.534109  
55   463.0  440.867920   423.0   0.527910          0.534303  
56   466.0  449.192322   432.0   0.528856          0.524745  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.530714  
42   466.0  447.942322   423.0   0.523173          0.529875  
43   466.0  445.075470   422.0   0.531036          0.535090  
44   466.0  448.442322   433.0   0.528190          0.527637  
45   466.0  443.923065   423.0   0.526241          0.526013  
46   466.0  447.750000   432.0   0.518024          0.521913  
47   466.0  447.961548   432.0   0.534486          0.530528  
48   456.0  438.596161   422.0   0.530303          0.530156  
49   456.0  439.924530   423.0   0.532754          0.528804  
50   466.0  444.924530   424.0   0.524686          0.527193  
51   466.0  442.150940   423.0   0.538614          0.536120  
52   466.0  447.923065   433.0   0.526741          0.527061  
53   436.0  419.134613   403.0   0.536859          0.533231  
54   456.0  439.480774   422.0   0.537116          0.535019  
55   463.0  440.867920   423.0   0.527910          0.534082  
56   466.0  449.192322   432.0   0.528856          0.521893  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.528138  
42   466.0  447.942322   423.0   0.523173          0.531066  
43   466.0  445.075470   422.0   0.531036          0.535281  
44   466.0  448.442322   433.0   0.528190          0.527842  
45   466.0  443.923065   423.0   0.526241          0.528751  
46   466.0  447.750000   432.0   0.518024          0.525844  
47   466.0  447.961548   432.0   0.534486          0.532261  
48   456.0  438.596161   422.0   0.530303          0.529630  
49   456.0  439.924530   423.0   0.532754          0.530892  
50   466.0  444.924530   424.0   0.524686          0.530351  
51   466.0  442.150940   423.0   0.538614          0.534973  
52   466.0  447.923065   433.0   0.526741          0.528916  
53   436.0  419.134613   403.0   0.536859          0.535638  
54   456.0  439.480774   422.0   0.537116          0.535502  
55   463.0  440.867920   423.0   0.527910          0.533243  
56   466.0  449.192322   432.0   0.528856          0.525249  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.528433  
42   466.0  447.942322   423.0   0.523173          0.530553  
43   466.0  445.075470   422.0   0.531036          0.535152  
44   466.0  448.442322   433.0   0.528190          0.525937  
45   466.0  443.923065   423.0   0.526241          0.529280  
46   466.0  447.750000   432.0   0.518024          0.525762  
47   466.0  447.961548   432.0   0.534486          0.534252  
48   456.0  438.596161   422.0   0.530303          0.531045  
49   456.0  439.924530   423.0   0.532754          0.528172  
50   466.0  444.924530   424.0   0.524686          0.529907  
51   466.0  442.150940   423.0   0.538614          0.529830  
52   466.0  447.923065   433.0   0.526741          0.525202  
53   436.0  419.134613   403.0   0.536859          0.533660  
54   456.0  439.480774   422.0   0.537116          0.531881  
55   463.0  440.867920   423.0   0.527910          0.533241  
56   466.0  449.192322   432.0   0.528856          0.525462  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.527787  
42   466.0  447.942322   423.0   0.523173          0.528594  
43   466.0  445.075470   422.0   0.531036          0.532561  
44   466.0  448.442322   433.0   0.528190          0.527787  
45   466.0  443.923065   423.0   0.526241          0.525485  
46   466.0  447.750000   432.0   0.518024          0.528272  
47   466.0  447.961548   432.0   0.534486          0.532864  
48   456.0  438.596161   422.0   0.530303          0.528272  
49   456.0  439.924530   423.0   0.532754          0.530839  
50   466.0  444.924530   424.0   0.524686          0.531318  
51   466.0  442.150940   423.0   0.538614          0.531560  
52   466.0  447.923065   433.0   0.526741          0.527787  
53   436.0  419.134613   403.0   0.536859          0.532561  
54   456.0  439.480774   422.0   0.537116          0.531840  
55   463.0  440.867920   423.0   0.527910          0.531560  
56   466.0  449.192322   432.0   0.528856          0.527787  
57   456.0  439.000000

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
42             1    1.0   91.0    0.0   45.0   11.0   67.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
44             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
45             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
46             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
47             1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
48             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
49             1    1.0   89.0    0.0   45.0   11.0   96.0   45.0   11.0   
50             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
51             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
52             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
53             1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
54             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
55             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
56             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
57             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
58             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
41   42.0  ...  188.625000  172.000000  202.199997  181.146423  170.399994   
42   42.0  ...  196.000000  181.399994  181.000000  177.864288  169.600006   
43   42.0  ...  188.796555  169.000000  171.899994  162.975861  153.899994   
44   42.0  ...  181.217850  161.100006  185.100006  167.035721  157.300003   
45   42.0  ...  197.317856  191.100006  174.500000  167.992859  161.800003   
46   42.0  ...  171.010712  163.100006  177.800003  167.967850  158.399994   
47   42.0  ...  181.596436  169.399994  184.000000  177.482147  170.100006   
48   42.0  ...  203.614288  188.199997  179.899994  168.828568  156.300003   
49   42.0  ...  209.631027  185.399994  188.399994  185.234482  179.800003   
50   42.0  ...  211.362076  195.699997  201.199997  191.286209  181.699997   
51   42.0  ...  191.520691  175.000000  168.100006  158.917236  145.399994   
52   42.0  ...  181.239288  171.100006  171.600006  167.725006  165.100006   
53   42.0  ...  198.242859  166.899994  197.100006  194.014282  188.600006   
54   42.0  ...  195.250000  182.399994  182.100006  168.932144  147.800003   
55   42.0  ...  209.417236  192.100006  192.000000  186.341385  175.100006   
56   42.0  ...  165.000000  155.000000  162.800003  158.524994  149.899994   
57   42.0  ...  191.037933  160.199997  183.000000  172.482758  161.199997   
58   42.0  ...  186.274994  165.000000  174.699997  166.457138  150.399994   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
41   466.0  450.673065   432.0   0.524808          0.526424  
42   466.0  447.942322   423.0   0.523173          0.520748  
43   466.0  445.075470   422.0   0.531036          0.542010  
44   466.0  448.442322   433.0   0.528190          0.530968  
45   466.0  443.923065   423.0   0.526241          0.529077  
46   466.0  447.750000   432.0   0.518024          0.525863  
47   466.0  447.961548   432.0   0.534486          0.541883  
48   456.0  438.596161   422.0   0.530303          0.530060  
49   456.0  439.924530   423.0   0.532754          0.529144  
50   466.0  444.924530   424.0   0.524686          0.531115  
51   466.0  442.150940   423.0   0.538614          0.532930  
52   466.0  447.923065   433.0   0.526741          0.526807  
53   436.0  419.134613   403.0   0.536859          0.536005  
54   456.0  439.480774   422.0   0.537116          0.537555  
55   463.0  440.867920   423.0   0.527910          0.535280  
56   466.0  449.192322   432.0   0.528856          0.519525  
57   456.0  439.000000

In [50]:
T010305_final_regression_model = finalize_model(T010305_model_xgb)

In [51]:
#최종 예측
#29
T010305_prediction = predict_model(T010305_final_regression_model, data=T010305_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [52]:
T010305_y_class = pd.DataFrame(T010305_class, columns = ['Y_Class'])
T010305_idx = T010305_y_class.index
T010305_y_class = T010305_y_class.reset_index()
T010305_prediction = pd.concat([T010305_prediction, T010305_y_class], axis = 1)
T010305_prediction = T010305_prediction.set_index('index')
T010305_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [53]:
#  and (T050307_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())
#  and (T010305_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [55]:
T010305_prediction['Y_Class'] = 22

T010305_idx = T010305_prediction.index
for i in range (len(T010305_prediction)) :
    if (T010305_prediction.iloc[i]['prediction_label'] <= (0.524808 +0.526241)/2) :
        T010305_prediction.loc[T010305_idx[i], 'Y_Class'] = 0
    elif ((0.524808 +0.526241)/2 < T010305_prediction.iloc[i]['prediction_label']) and (T010305_prediction.iloc[i]['prediction_label'] < (0.534486+0.535741)/2) :
        T010305_prediction.loc[T010305_idx[i], 'Y_Class'] = 1
    elif ((0.534486+0.535741)/2 <= T010305_prediction.iloc[i]['prediction_label']) :
        T010305_prediction.loc[T010305_idx[i], 'Y_Class'] = 2
T010305_prediction

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
index                                                                         
28                1    1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   
33                1    1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   
39                1    1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   
40                1    1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   
41                1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   
48                1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
52                1    2.0   87.0    0.0   45.0   11.0  114.0   45.0   11.0   
57                1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
58                1    1.0   88.0    0.0   45.0   11.0  119.0   45.0   11.0   
59                1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
64                1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
65                1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
66                1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
69                1    2.0   91.0    0.0   45.0   11.0  129.0   45.0   11.0   
71                1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
75                1    2.0   89.0    0.0   45.0   11.0  135.0   45.0   11.0   
77                1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
84                1    1.0   95.0    0.0   45.0   11.0  155.0   45.0   11.0   
90                1    2.0   89.0    0.0   45.0   11.0  163.0   45.0   11.0   
94                1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
95                1    2.0   90.0    0.0   45.0   11.0  168.0   45.0   11.0   
116               1    1.0   95.0    0.0   45.0   11.0    2.0   45.0   11.0   
118               1    1.0   91.0    0.0   45.0   11.0    2.0   45.0   12.0   
123               1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
129               1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
179               1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
190               1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
208               1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   
220               1    2.0   93.0    0.0   45.0   11.0   34.0   45.0   11.0   
230               1    2.0   91.0    0.0   45.0   11.0   38.0   45.0   11.0   
235               1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
239               1    2.0   88.0    0.0   45.0   11.0   44.0   45.0   11.0   
244               1    1.0   90.0    0.0   45.0   11.0   46.0   45.0   11.0   
281               1    2.0   88.0    0.0   45.0   11.0   85.0   45.0   11.0   
283               1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
287               1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
291               1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
292               1    1.0   89.0    0.0   45.0   11.0   89.0   45.0   11.0   
295               1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
299               1    1.0   96.0    0.0   45.0   11.0   93.0   45.0   11.0   
300               1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
312               1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
332               1    1.0   90.0    0.0   45.0   11.0  111.0   45.0   11.0   
334               1    2.0   88.0    0.0   45.0   11.0  111.0   45.0   11.0   
404               1    1.0   90.0    0.0   45.0   11.0   14.0   45.0   11.0   
410               1    1.0   88.0    0.0   45.0   11.0   19.0   45.0   11.0   
436               1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
449               1   11.0   90.0    0.0   45.0   11.0   43.0   45.0   11.0   
455               1    1.0   89.0    0.0   45.0   11.0   

In [56]:
T010305_prediction['Y_Class'].unique()

array([0, 1, 2], dtype=int64)

# T010306

In [57]:
T010306_class = T010306['Y_Class']
T010306_target = T010306['Y_Quality']
T010306_data = T010306.drop(['Y_Class', 'Y_Quality'], axis = 1)
T010306_data

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
27              1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
31              1    4.0   93.0  150.0   45.0   12.0    0.0   45.0   12.0   
32              1    1.0   89.0  152.0   45.0   12.0    0.0   45.0   12.0   
38              1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
47              1    1.0   95.0  166.0   45.0   11.0    0.0   45.0   12.0   
..            ...    ...    ...    ...    ...    ...    ...    ...    ...   
479             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
501             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
523             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
531             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
585             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   

     X_254  ...  X_2856  X_2857      X_2858  X_2859  X_2860      X_2861  \
27    51.0  ...   177.1   186.2  169.907143   156.5   188.4  175.225000   
31    51.0  ...   170.8   207.8  191.775862   166.0   195.1  188.696552   
32    51.0  ...   174.5   190.7  181.686207   172.7   180.0  168.775862   
38    51.0  ...   167.9   200.3  187.339286   180.1   184.3  177.528571   
47    51.0  ...   173.1   203.7  188.434483   165.3   185.9  173.596552   
..     ...  ...     ...     ...         ...     ...     ...         ...   
479   51.0  ...   199.7   222.6  193.278571   177.5   183.3  169.553571   
501   51.0  ...   196.1   211.1  197.392857   173.1   187.6  182.142857   
523   51.0  ...   203.2   205.1  194.860714   183.9   189.2  181.700000   
531   51.0  ...   189.0   201.3  190.407143   181.1   192.6  185.207143   
585   51.0  ...   204.1   216.0  205.079310   196.1   192.2  187.396552   

     X_2862  X_2863      X_2864  X_2865  
27    159.9   446.0  430.442308   413.0  
31    181.7   446.0  429.245283   413.0  
32    154.1   446.0  429.981132   415.0  
38    166.6   446.0  426.250000   404.0  
47    157.2   447.0  429.905660   413.0  
..      ...     ...         ...     ...  
479   154.2   456.0  438.132075   413.0  
501   175.1   466.0  445.307692   425.0  
523   172.7   466.0  444.615385   423.0  
531   173.2   466.0  446.038461   427.0  
585   176.7   472.0  450.339623   432.0  

[70 rows x 887 columns]

In [58]:
#13
setup_rgs = setup(data = T010306_data, target=T010306_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [61]:
T010306_total_models = []

T010306_model_ada = create_model('ada', fold = 5)
T010306_total_models.append(T010306_model_ada)

T010306_model_gbr = create_model('gbr', fold = 5)
T010306_total_models.append(T010306_model_gbr)

T010306_model_et = create_model('et', fold = 5)
T010306_total_models.append(T010306_model_et)

T010306_model_catboost = create_model('catboost', fold = 5)
T010306_total_models.append(T010306_model_catboost)

T010306_model_xgb = create_model('xgboost', fold = 5)
T010306_total_models.append(T010306_model_xgb)

T010306_model_rf = create_model('rf', fold = 5)
T010306_total_models.append(T010306_model_rf)

T010306_model_lightgbm = create_model('lightgbm', fold = 5)
T010306_total_models.append(T010306_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [62]:
T010306_model_ada = tune_model(T010306_model_ada, fold=5, choose_better = True)

T010306_model_gbr = tune_model(T010306_model_gbr, fold=5, choose_better = True)

T010306_model_et = tune_model(T010306_model_et, fold=5, choose_better = True)

T010306_model_catboost = tune_model(T010306_model_catboost, fold=5, choose_better = True)

T010306_model_xgb = tune_model(T010306_model_xgb, fold=5, choose_better = True)

T010306_model_rf = tune_model(T010306_model_rf, fold=5, choose_better = True)

T010306_model_lightgbm = tune_model(T010306_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [63]:
T010306_tuned_models = [T010306_model_ada, T010306_model_gbr, T010306_model_et, T010306_model_catboost, T010306_model_xgb, T010306_model_rf, T010306_model_lightgbm]
T010306_tuned_models

[AdaBoostRegressor(learning_rate=0.1, loss='exponential', n_estimators=170,
                   random_state=414),
 GradientBoostingRegressor(random_state=414),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
              reg_alpha=0, reg_lambda=1, ...),
 RandomForestRegressor(n_jobs=-1, random_state=414),
 LGBMRegressor(random_state=414)]

In [64]:
for model in T010306_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.530454  
50   456.0  438.679260   423.0   0.522121          0.530606  
51   472.0  450.339630   432.0   0.515214          0.531339  
52   457.0  440.320740   422.0   0.554562          0.537864  
53   466.0  444.615387   423.0   0.534640          0.532487  
54   456.0  439.396240   415.0   0.528087          0.531850  
55   466.0  442.576935   423.0   0.547497          0.547308  
56   466.0  446.038452   427.0   0.560317          0.539546  
57   456.0  439.339630   423.0   0.538502          0.534

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.528162  
50   456.0  438.679260   423.0   0.522121          0.530715  
51   472.0  450.339630   432.0   0.515214          0.529458  
52   457.0  440.320740   422.0   0.554562          0.538821  
53   466.0  444.615387   423.0   0.534640          0.532860  
54   456.0  439.396240   415.0   0.528087          0.531056  
55   466.0  442.576935   423.0   0.547497          0.547017  
56   466.0  446.038452   427.0   0.560317          0.547977  
57   456.0  439.339630   423.0   0.538502          0.540

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.532890  
50   456.0  438.679260   423.0   0.522121          0.527700  
51   472.0  450.339630   432.0   0.515214          0.529064  
52   457.0  440.320740   422.0   0.554562          0.547177  
53   466.0  444.615387   423.0   0.534640          0.535484  
54   456.0  439.396240   415.0   0.528087          0.534939  
55   466.0  442.576935   423.0   0.547497          0.547518  
56   466.0  446.038452   427.0   0.560317          0.546192  
57   456.0  439.339630   423.0   0.538502          0.539

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.534381  
50   456.0  438.679260   423.0   0.522121          0.530861  
51   472.0  450.339630   432.0   0.515214          0.533326  
52   457.0  440.320740   422.0   0.554562          0.540661  
53   466.0  444.615387   423.0   0.534640          0.535808  
54   456.0  439.396240   415.0   0.528087          0.533262  
55   466.0  442.576935   423.0   0.547497          0.544183  
56   466.0  446.038452   427.0   0.560317          0.541293  
57   456.0  439.339630   423.0   0.538502          0.535

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.534986  
50   456.0  438.679260   423.0   0.522121          0.531540  
51   472.0  450.339630   432.0   0.515214          0.530692  
52   457.0  440.320740   422.0   0.554562          0.547435  
53   466.0  444.615387   423.0   0.534640          0.533440  
54   456.0  439.396240   415.0   0.528087          0.535293  
55   466.0  442.576935   423.0   0.547497          0.542213  
56   466.0  446.038452   427.0   0.560317          0.540545  
57   456.0  439.339630   423.0   0.538502          0.536

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.532928  
50   456.0  438.679260   423.0   0.522121          0.530993  
51   472.0  450.339630   432.0   0.515214          0.531642  
52   457.0  440.320740   422.0   0.554562          0.540473  
53   466.0  444.615387   423.0   0.534640          0.532803  
54   456.0  439.396240   415.0   0.528087          0.532974  
55   466.0  442.576935   423.0   0.547497          0.539203  
56   466.0  446.038452   427.0   0.560317          0.539120  
57   456.0  439.339630   423.0   0.538502          0.532

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   83.0   45.0   12.0    0.0   45.0   12.0   
50             1    1.0   89.0    7.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
52             1    1.0   90.0  103.0   45.0   11.0    0.0   45.0   12.0   
53             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
54             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   96.0   95.0   45.0   12.0    0.0   45.0   12.0   
56             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
57             1    1.0   94.0  118.0   45.0   12.0    0.0   45.0   12.0   
58             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
59             1    2.0   88.0   83.0   45.0   11.0    0.0   45.0   12.0   
60             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
61             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
62             1    1.0   93.0   73.0   45.0   11.0    0.0   45.0   12.0   
63             1    1.0   95.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
65             1    1.0   88.0   83.0   45.0   12.0    0.0   45.0   12.0   
66             1    2.0   93.0   85.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   92.0  152.0   45.0   11.0    0.0   45.0   12.0   
68             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
69             1    1.0   96.0   27.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
49   51.0  ...  176.065521  159.600006  182.800003  170.372421  162.100006   
50   51.0  ...  193.558624  181.399994  167.000000  158.520691  148.000000   
51   51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   
52   51.0  ...  198.279312  180.600006  186.899994  176.134476  162.899994   
53   51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
54   51.0  ...  196.762070  188.399994  188.300003  177.379303  166.600006   
55   51.0  ...  174.921432  169.600006  184.899994  177.839279  169.199997   
56   51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
57   51.0  ...  174.879303  167.600006  173.300003  165.455170  151.199997   
58   51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
59   51.0  ...  184.375000  175.800003  175.399994  165.489288  151.000000   
60   51.0  ...  198.853577  184.100006  180.399994  169.782150  161.500000   
61   51.0  ...  188.834488  172.000000  183.600006  171.437927  163.899994   
62   51.0  ...  189.113800  173.800003  164.100006  159.762070  154.899994   
63   51.0  ...  180.368973  174.000000  172.300003  160.806900  144.300003   
64   51.0  ...  200.124146  189.100006  184.800003  178.096558  166.300003   
65   51.0  ...  163.617859  155.100006  176.000000  162.321426  153.300003   
66   51.0  ...  178.035721  168.000000  200.399994  187.314285  177.300003   
67   51.0  ...  185.437927  165.899994  178.000000  169.148270  151.800003   
68   51.0  ...  189.582138  177.399994  170.500000  153.157150  143.899994   
69   51.0  ...  185.028564  181.000000  189.199997  183.953568  179.500000   

    X_2863      X_2864  X_2865  Y_Quality  prediction_label  
49   466.0  449.018860   428.0   0.527689          0.536951  
50   456.0  438.679260   423.0   0.522121          0.529629  
51   472.0  450.339630   432.0   0.515214          0.533524  
52   457.0  440.320740   422.0   0.554562          0.535682  
53   466.0  444.615387   423.0   0.534640          0.534518  
54   456.0  439.396240   415.0   0.528087          0.537118  
55   466.0  442.576935   423.0   0.547497          0.544400  
56   466.0  446.038452   427.0   0.560317          0.538005  
57   456.0  439.339630   423.0   0.538502          0.537

In [65]:
T010306_final_regression_model = finalize_model(T010306_model_xgb)

In [66]:
#최종 예측
#29
T010306_prediction = predict_model(T010306_final_regression_model, data=T010306_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [67]:
T010306_y_class = pd.DataFrame(T010306_class, columns = ['Y_Class'])
T010306_idx = T010306_y_class.index
T010306_y_class =T010306_y_class.reset_index()
T010306_prediction = pd.concat([T010306_prediction, T010306_y_class], axis = 1)
T010306_prediction = T010306_prediction.set_index('index')
T010306_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [68]:
#(train_data[train_data['Y_Class'] == 0]['Y_Quality'].min() <= T010306_prediction.iloc[i]['prediction_label']) and 
#and (T010306_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [69]:
T010306_prediction['Y_Class'] = 22

T010306_idx = T010306_prediction.index
for i in range (len(T010306_prediction)) :
    if (T010306_prediction.iloc[i]['prediction_label'] <= (0.524487+0.525221)/2) :
        T010306_prediction.loc[T010306_idx[i], 'Y_Class'] = 0
    elif ((0.524487+0.525221)/2 < T010306_prediction.iloc[i]['prediction_label']) and (T010306_prediction.iloc[i]['prediction_label'] < (0.534737+0.535279)/2) :
        T010306_prediction.loc[T010306_idx[i], 'Y_Class'] = 1
    elif ((0.534737+0.535279)/2 <= T010306_prediction.iloc[i]['prediction_label'])  :
        T010306_prediction.loc[T010306_idx[i], 'Y_Class'] = 2
T010306_prediction

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
index                                                                         
27                1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
31                1    4.0   93.0  150.0   45.0   12.0    0.0   45.0   12.0   
32                1    1.0   89.0  152.0   45.0   12.0    0.0   45.0   12.0   
38                1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
47                1    1.0   95.0  166.0   45.0   11.0    0.0   45.0   12.0   
...             ...    ...    ...    ...    ...    ...    ...    ...    ...   
479               1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
501               1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
523               1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
531               1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
585               1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   

       X_254  ...      X_2858      X_2859      X_2860      X_2861      X_2862  \
index         ...                                                               
27      51.0  ...  169.907150  156.500000  188.399994  175.225006  159.899994   
31      51.0  ...  191.775864  166.000000  195.100006  188.696548  181.699997   
32      51.0  ...  181.686203  172.699997  180.000000  168.775864  154.100006   
38      51.0  ...  187.339279  180.100006  184.300003  177.528564  166.600006   
47      51.0  ...  188.434479  165.300003  185.899994  173.596558  157.199997   
...      ...  ...         ...         ...         ...         ...         ...   
479     51.0  ...  193.278564  177.500000  183.300003  169.553574  154.199997   
501     51.0  ...  197.392853  173.100006  187.600006  182.142853  175.100006   
523     51.0  ...  194.860718  183.899994  189.199997  181.699997  172.699997   
531     51.0  ...  190.407150  181.100006  192.600006  185.207138  173.199997   
585     51.0  ...  205.079315  196.100006  192.199997  187.396545  176.699997   

       X_2863      X_2864  X_2865  prediction_label  Y_Class  
index                                                         
27      446.0  430.442322   413.0          0.539756        2  
31      446.0  429.245270   413.0          0.536183        2  
32      446.0  429.981140   415.0          0.548343        2  
38      446.0  426.250000   404.0          0.536574        2  
47      447.0  429.905670   413.0          0.533248        1  
...       ...         ...     ...               ...      ...  
479     456.0  438.132080   413.0          0.534814        1  
501     466.0  445.307678   425.0          0.533238        1  
523     466.0  444.615387   423.0          0.534728        1  
531     466.0  446.038452   427.0          0.559187        2  
585     472.0  450.339630   432.0          0.515877        0  

[70 rows x 889 columns]

In [70]:
T010306_prediction['Y_Class'].unique()

array([2, 1, 0], dtype=int64)

# T100304

In [71]:
T100304_class = T100304['Y_Class']
T100304_target = T100304['Y_Quality']
T100304_data = T100304.drop(['Y_Class', 'Y_Quality'], axis = 1)
T100304_data

PRODUCT_CODE   X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
22              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
23              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
25              2   2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
29              2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
37              2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
..            ...   ...    ...  ...   ...   ...  ...   ...   ...   ...  ...   
561             2   2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
569             3   4.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
571             3   4.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
592             2   2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
596             3  40.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   

     X_924  X_925       X_926  X_927  X_928       X_929  X_930  X_931  \
22   172.5  162.8  157.235484  150.9  326.0  309.290909  290.0   13.7   
23     0.0    0.0    0.000000    0.0    0.0    0.000000    0.0    0.0   
25   177.8  157.1  154.074194  150.9  327.0  310.854546  298.0   13.7   
29   177.9  161.3  156.038710  149.1  327.0  312.109091  298.0   13.7   
37   182.8  162.9  155.829032  148.4  327.0  312.254546  298.0   13.7   
..     ...    ...         ...    ...    ...         ...    ...    ...   
561  164.1  162.6  156.932258  151.1  317.0  303.527273  289.0   13.7   
569  181.7  160.0  155.541935  149.8  327.0  312.018182  298.0   13.6   
571  175.4  165.7  159.864516  148.7  326.0  311.763636  298.0   13.7   
592  171.5  156.6  152.535484  147.6  326.0  312.472727  298.0   13.6   
596  189.2  179.5  173.190323  168.6  321.0  303.036364  289.0   13.6   

         X_932  X_933  
22   13.443333   13.2  
23    0.000000    0.0  
25   13.454839   13.2  
29   13.422581   13.2  
37   13.456667   13.3  
..         ...    ...  
561  13.470000   13.3  
569  13.458065   13.3  
571  13.425806   13.2  
592  13.361290   13.2  
596  13.406667   13.2  

[175 rows x 672 columns]

In [72]:
setup_rgs = setup(data = T100304_data, target=T100304_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [73]:
T100304_total_models = []

T100304_model_rf = create_model('rf', fold = 5)
T100304_total_models.append(T100304_model_rf)

T100304_model_gbr = create_model('gbr', fold = 5)
T100304_total_models.append(T100304_model_gbr)

T100304_model_et = create_model('et', fold = 5)
T100304_total_models.append(T100304_model_et)

T100304_model_catboost = create_model('catboost', fold = 5)
T100304_total_models.append(T100304_model_catboost)

T100304_model_xgb = create_model('xgboost', fold = 5)
T100304_total_models.append(T100304_model_xgb)

T100304_model_ada = create_model('ada', fold = 5)
T100304_total_models.append(T100304_model_ada)

T100304_model_lightgbm = create_model('lightgbm', fold = 5)
T100304_total_models.append(T100304_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [74]:
T100304_model_lightgbm = tune_model(T100304_model_lightgbm, fold=5, choose_better = True)

T100304_model_gbr = tune_model(T100304_model_gbr, fold=5, choose_better = True)

T100304_model_et = tune_model(T100304_model_et, fold=5, choose_better = True)

T100304_model_catboost = tune_model(T100304_model_catboost, fold=5, choose_better = True)

T100304_model_xgb = tune_model(T100304_model_xgb, fold=5, choose_better = True)

T100304_model_ada = tune_model(T100304_model_ada, fold=5, choose_better = True)

T100304_model_rf = tune_model(T100304_model_rf, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [75]:
T100304_tuned_models = [T100304_model_lightgbm, T100304_model_gbr, T100304_model_et, T100304_model_catboost, T100304_model_xgb, T100304_model_ada, T100304_model_rf]
T100304_tuned_models

[LGBMRegressor(bagging_fraction=0.8, bagging_freq=2, feature_fraction=0.7,
               learning_rate=0.005, min_child_samples=1, min_split_gain=0.6,
               n_estimators=30, num_leaves=40, random_state=414, reg_alpha=0.1,
               reg_lambda=10),
 GradientBoostingRegressor(learning_rate=0.15, max_depth=8, max_features='sqrt',
                           min_impurity_decrease=0.0001, min_samples_leaf=2,
                           min_samples_split=4, n_estimators=210,
                           random_state=414, subsample=0.6),
 ExtraTreesRegressor(criterion='absolute_error', max_depth=2,
                     max_features='log2', min_impurity_decrease=0,
                     min_samples_leaf=6, min_samples_split=9, n_estimators=160,
                     n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=0.5,
              early_stopping_rounds=None, enable_ca

In [76]:
for model in T100304_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
132             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
133             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    1.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
140             2    2.0  102.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
151             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    1.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

In [77]:
T100304_final_regression_model = finalize_model(T100304_model_catboost)

In [78]:
#최종 예측
#29
T100304_prediction = predict_model(T100304_final_regression_model, data=T100304_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [79]:
T100304_y_class = pd.DataFrame(T100304_class, columns = ['Y_Class'])
T100304_idx = T100304_y_class.index
T100304_y_class =T100304_y_class.reset_index()
T100304_prediction = pd.concat([T100304_prediction, T100304_y_class], axis = 1)
T100304_prediction = T100304_prediction.set_index('index')
T100304_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [80]:
# (train_data[train_data['Y_Class'] == 0]['Y_Quality'].min() <= T100304_prediction.iloc[i]['prediction_label']) and 
# and (T100304_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [81]:
T100304_prediction['Y_Class'] = 22

T100304_idx = T100304_prediction.index
for i in range (len(T100304_prediction)) :
    if (T100304_prediction.iloc[i]['prediction_label'] <= (0.525035+0.525483)/2) :
        T100304_prediction.loc[T100304_idx[i], 'Y_Class'] = 0
    elif ((0.525035+0.525483)/2 < T100304_prediction.iloc[i]['prediction_label']) and (T100304_prediction.iloc[i]['prediction_label'] < (0.534837+0.534951)/2) :
        T100304_prediction.loc[T100304_idx[i], 'Y_Class'] = 1
    elif ((0.534837+0.534951)/2 <= T100304_prediction.iloc[i]['prediction_label']) :
        T100304_prediction.loc[T100304_idx[i], 'Y_Class'] = 2
T100304_prediction

PRODUCT_CODE   X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
index                                                                     ...   
22                2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
23                2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
25                2   2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
29                2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
37                2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
...             ...   ...    ...  ...   ...   ...  ...   ...   ...   ...  ...   
561               2   2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
569               3   4.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
571               3   4.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
592               2   2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
596               3  40.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   

            X_926       X_927  X_928       X_929  X_930  X_931      X_932  \
index                                                                       
22     157.235489  150.899994  326.0  309.290924  290.0   13.7  13.443334   
23       0.000000    0.000000    0.0    0.000000    0.0    0.0   0.000000   
25     154.074188  150.899994  327.0  310.854553  298.0   13.7  13.454839   
29     156.038712  149.100006  327.0  312.109100  298.0   13.7  13.422581   
37     155.829025  148.399994  327.0  312.254547  298.0   13.7  13.456667   
...           ...         ...    ...         ...    ...    ...        ...   
561    156.932251  151.100006  317.0  303.527283  289.0   13.7  13.470000   
569    155.541931  149.800003  327.0  312.018188  298.0   13.6  13.458064   
571    159.864517  148.699997  326.0  311.763641  298.0   13.7  13.425806   
592    152.535477  147.600006  326.0  312.472717  298.0   13.6  13.361290   
596    173.190323  168.600006  321.0  303.036377  289.0   13.6  13.406667   

       X_933  prediction_label  Y_Class  
index                                    
22      13.2          0.517794        0  
23       0.0          0.519140        0  
25      13.2          0.529405        1  
29      13.2          0.532299        1  
37      13.3          0.533052        1  
...      ...               ...      ...  
561     13.3          0.522207        0  
569     13.3          0.530515        1  
571     13.2          0.525979        1  
592     13.2          0.528388        1  
596     13.2          0.531352        1  

[175 rows x 674 columns]

In [82]:
T100304_prediction['Y_Class'].unique()

array([0, 1, 2], dtype=int64)

# T100306

In [83]:
T100306_class = T100306['Y_Class']
T100306_target = T100306['Y_Quality']
T100306_data = T100306.drop(['Y_Class', 'Y_Quality'], axis = 1)
T100306_data

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
26              2   2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
30              2   2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
36              2   2.0  91.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
42              2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
43              2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
..            ...   ...   ...  ...   ...   ...  ...   ...   ...   ...  ...   
589             2   1.0  94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
590             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
591             2   1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
593             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
597             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   

     X_924  X_925       X_926  X_927  X_928       X_929  X_930  X_931  \
26   166.9  158.5  151.096774  146.5  327.0  313.618182  299.0   13.7   
30   174.5  161.1  153.574194  147.6  327.0  313.109091  297.0   13.7   
36   179.3  157.7  151.890323  146.1  327.0  309.636364  292.0   13.7   
42   176.0  160.3  155.129032  151.0  327.0  312.553571  298.0   13.7   
43   183.1  165.1  159.100000  155.0  326.0  305.370370  288.0   13.7   
..     ...    ...         ...    ...    ...         ...    ...    ...   
589  170.1  159.9  154.309677  149.1  326.0  311.272727  298.0   13.7   
590  176.2  158.1  154.812903  150.0  327.0  313.400000  299.0   13.6   
591  177.0  159.6  154.777419  147.7  326.0  313.472727  298.0   13.6   
593  172.8  161.2  155.438710  149.0  327.0  313.363636  298.0   13.6   
597  188.2  172.9  167.087097  161.1  326.0  304.818182  289.0   13.6   

         X_932  X_933  
26   13.461290   13.3  
30   13.376667   13.2  
36   13.454839   13.3  
42   13.503333   13.3  
43   13.446667   13.2  
..         ...    ...  
589  13.483871   13.3  
590  13.393548   13.2  
591  13.400000   13.2  
593  13.351613   13.2  
597  13.380000   13.2  

[174 rows x 672 columns]

In [84]:
setup_rgs = setup(data = T100306_data, target=T100306_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [85]:
T100306_total_models = []

T100306_model_rf = create_model('rf', fold = 5)
T100306_total_models.append(T100306_model_rf)

T100306_model_gbr = create_model('gbr', fold = 5)
T100306_total_models.append(T100306_model_gbr)

T100306_model_et = create_model('et', fold = 5)
T100306_total_models.append(T100306_model_et)

T100306_model_catboost = create_model('catboost', fold = 5)
T100306_total_models.append(T100306_model_catboost)

T100306_model_xgb = create_model('xgboost', fold = 5)
T100306_total_models.append(T100306_model_xgb)

T100306_model_ada = create_model('ada', fold = 5)
T100306_total_models.append(T100306_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [86]:
T100306_model_lightgbm = tune_model(T100306_model_rf, fold=5, choose_better = True)

T100306_model_gbr = tune_model(T100306_model_gbr, fold=5, choose_better = True)

T100306_model_et = tune_model(T100306_model_et, fold=5, choose_better = True)

T100306_model_catboost = tune_model(T100306_model_catboost, fold=5, choose_better = True)

T100306_model_xgb = tune_model(T100306_model_xgb, fold=5, choose_better = True)

T100306_model_ada = tune_model(T100306_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [87]:
T100306_tuned_models = [T100306_model_rf, T100306_model_gbr, T100306_model_et, T100306_model_catboost, T100306_model_xgb, T100306_model_ada]
T100306_tuned_models

[RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(learning_rate=0.2, max_depth=1, max_features='sqrt',
                           min_impurity_decrease=0.002, min_samples_split=7,
                           n_estimators=110, random_state=414, subsample=0.45),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
   

In [88]:
for model in T100306_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2  1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
124             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
125             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
126             2  1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
127             2  2.0  91.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
128             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
129             2  2.0  91.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2  2.0  91.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
131             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
132             2  2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
133             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
134             2  3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
135             2  2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
136             2  2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
137             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
138             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
139             2  1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
140             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
141             2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
142             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
143             2  2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
145             2  2.0  96.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
146             2  2.0  94.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
147             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
148             2  2.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
150             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
152             2  2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
153             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
154             2  1.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2  2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
156             2  1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
157             2  2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
158             2  2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
159             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
160             2  2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
161             2  2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
162             2  2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
163             2  2.0  95.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
164             2  2.0  96.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
165             2  2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
166             2  2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
167             2  1.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
168             2  2.0  91.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
169             2  2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
170             2  2.0  94.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
171             2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
1

In [89]:
T100306_final_regression_model = finalize_model(T100306_model_et)

In [90]:
#최종 예측
#29
T100306_prediction = predict_model(T100306_final_regression_model, data=T100306_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [91]:
T100306_y_class = pd.DataFrame(T100306_class, columns = ['Y_Class'])
T100306_idx = T100306_y_class.index
T100306_y_class =T100306_y_class.reset_index()
T100306_prediction = pd.concat([T100306_prediction, T100306_y_class], axis = 1)
T100306_prediction = T100306_prediction.set_index('index')
T100306_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [92]:
#(train_data[train_data['Y_Class'] == 0]['Y_Quality'].min() <= T100306_prediction.iloc[i]['prediction_label']) and 
# and (T100306_prediction.iloc[i]['prediction_label'] <= train_data[train_data['Y_Class'] == 2]['Y_Quality'].max())

In [93]:
T100306_prediction['Y_Class'] = 22

T100306_idx = T100306_prediction.index
for i in range (len(T100306_prediction)) :
    if (T100306_prediction.iloc[i]['prediction_label'] <= (0.525067 +0.525213 )/2) :
        T100306_prediction.loc[T100306_idx[i], 'Y_Class'] = 0
    elif ((0.525067 +0.525213 )/2 < T100306_prediction.iloc[i]['prediction_label']) and (T100306_prediction.iloc[i]['prediction_label'] < (0.534737+0.534951 )/2) :
        T100306_prediction.loc[T100306_idx[i], 'Y_Class'] = 1
    elif ((0.534737+0.534951 )/2 <= T100306_prediction.iloc[i]['prediction_label']) :
        T100306_prediction.loc[T100306_idx[i], 'Y_Class'] = 2
T100306_prediction

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
index                                                                    ...   
26                2   2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
30                2   2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
36                2   2.0  91.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
42                2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
43                2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
...             ...   ...   ...  ...   ...   ...  ...   ...   ...   ...  ...   
589               2   1.0  94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
590               2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
591               2   1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
593               2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
597               3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   

            X_926       X_927  X_928       X_929  X_930  X_931      X_932  \
index                                                                       
26     151.096771  146.500000  327.0  313.618195  299.0   13.7  13.461290   
30     153.574188  147.600006  327.0  313.109100  297.0   13.7  13.376667   
36     151.890320  146.100006  327.0  309.636353  292.0   13.7  13.454839   
42     155.129028  151.000000  327.0  312.553558  298.0   13.7  13.503333   
43     159.100006  155.000000  326.0  305.370361  288.0   13.7  13.446667   
...           ...         ...    ...         ...    ...    ...        ...   
589    154.309677  149.100006  326.0  311.272736  298.0   13.7  13.483871   
590    154.812897  150.000000  327.0  313.399994  299.0   13.6  13.393548   
591    154.777420  147.699997  326.0  313.472717  298.0   13.6  13.400000   
593    155.438705  149.000000  327.0  313.363647  298.0   13.6  13.351613   
597    167.087097  161.100006  326.0  304.818176  289.0   13.6  13.380000   

       X_933  prediction_label  Y_Class  
index                                    
26      13.3          0.531992        1  
30      13.2          0.528646        1  
36      13.3          0.529633        1  
42      13.3          0.530965        1  
43      13.2          0.529498        1  
...      ...               ...      ...  
589     13.3          0.529510        1  
590     13.2          0.529948        1  
591     13.2          0.529308        1  
593     13.2          0.526546        1  
597     13.2          0.533702        1  

[174 rows x 674 columns]

In [94]:
T100306_prediction['Y_Class'].unique()

array([1, 0, 2], dtype=int64)

# Test

In [110]:
#44
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [241]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [111]:
test_data.drop(colls, inplace = True, axis = 1)

In [243]:
test_data = test_data.drop(['MONTH', 'MINUTE', 'DAY', 'YEAR'], axis = 1)

In [112]:
'''
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7
'''
test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  \
0       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
3     183.8   467.0  444.192308   423.0     NaN     NaN     NaN     NaN   
4     179.7   465.0  443.211539   423.0     NaN     NaN     NaN     NaN   
..      ...     ...         ...     ...     ...     ...     ...     ...   
305     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   

     X_2870  X_2871  
0       NaN     NaN  
1       NaN     NaN  
2       NaN     NaN  
3       NaN     NaN  
4       NaN     NaN  
..      ...     ...  
305     NaN     NaN  
306     NaN     NaN  
307     NaN     NaN  
308     NaN     NaN  
309     NaN     NaN  

[310 rows x 2795 columns]

In [113]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  X_2862  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   168.3   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   169.8   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   139.5   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   103.5   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   165.6   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   171.8   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   161.0   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   175.1   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   175.1   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   115.9   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   147.1   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   118.9   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   177.0   

    X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  
7    384.0  369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0  
8    384.0  370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0  
14   384.0  369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0  
35   384.0  369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0  
41   383.0  368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0  
42   384.0  368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0  
52   384.0  368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0  
53   384.0  361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0  
54   384.0  367.849057   352.0   55.72   57.57   42.08   55.19   66.06     1.0  
61   384.0  370.000000   354.0     NaN     NaN     NaN     NaN     NaN     1.0  
64   384.0  367.943396   352.0     NaN     NaN     NaN     NaN     NaN     1.0  
65   383.0  368.056604   352.0   51.55   55.55   39.85   47.82   61.59     1.0  
66   384.0  369.111111   353.0   51.37   55.70   52.49   48.34   62.12     1.0  

[13 rows x 2795 columns]

In [114]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [115]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
7   354.0  ...   168.3   384.0  369.462963   354.0   57.74   52.51   54.45   
8   355.0  ...   169.8   384.0  370.259259   353.0   53.18   56.02   41.79   
14   60.0  ...   139.5   384.0  369.377359   353.0   49.77   54.93   49.85   
35  249.0  ...   103.5   384.0  369.660377   352.0   55.22   58.14   48.93   
41  293.0  ...   165.6   383.0  368.018519   352.0   49.67   45.00   49.81   
42  293.0  ...   171.8   384.0  368.452830   353.0   51.30   47.66   60.00   
52  330.0  ...   161.0   384.0  368.320755   353.0   54.06   51.18   52.17   
53  330.0  ...   175.1   384.0  361.226415   342.0   54.04   51.25   54.98   
54  330.0  ...   175.1   384.0  367.849057   352.0   55.72   57.57   42.08   
61  436.0  ...   115.9   384.0  370.000000   354.0     NaN     NaN     NaN   
64  437.0  ...   147.1   384.0  367.943396   352.0     NaN     NaN     NaN   
65  441.0  ...   118.9   383.0  368.056604   352.0   51.55   55.55   39.85   
66  446.0  ...   177.0   384.0  369.111111   353.0   51.37   55.70   52.49   

    X_2869  X_2870  X_2871  
7    57.99   63.16     1.0  
8    47.94   60.72     1.0  
14   48.62   63.18     1.0  
35   56.16   64.25     1.0  
41   55.19   67.17     1.0  
42   53.75   62.58     1.0  
52   57.75   63.94     1.0  
53   57.22   63.33     1.0  
54   55.19   66.06     1.0  
61     NaN     NaN     1.0  
64     NaN     NaN     1.0  
65   47.82   61.59     1.0  
66   48.34   62.12     1.0  

[13 rows x 1969 columns]

In [116]:
TT050304 = TT050304.fillna(0)
TT050307 = TT050307.fillna(0)
TT010305 = TT010305.fillna(0)
TT010306 = TT010306.fillna(0)
TT100304 = TT100304.fillna(0)
TT100306 = TT100306.fillna(0)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7              1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8              1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14             1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35             1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41             1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42             1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52             1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53             1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54             1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61             1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64             1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65             1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66             1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
7   354.0  ...   168.3   384.0  369.462963   354.0   57.74   52.51   54.45   
8   355.0  ...   169.8   384.0  370.259259   353.0   53.18   56.02   41.79   
14   60.0  ...   139.5   384.0  369.377359   353.0   49.77   54.93   49.85   
35  249.0  ...   103.5   384.0  369.660377   352.0   55.22   58.14   48.93   
41  293.0  ...   165.6   383.0  368.018519   352.0   49.67   45.00   49.81   
42  293.0  ...   171.8   384.0  368.452830   353.0   51.30   47.66   60.00   
52  330.0  ...   161.0   384.0  368.320755   353.0   54.06   51.18   52.17   
53  330.0  ...   175.1   384.0  361.226415   342.0   54.04   51.25   54.98   
54  330.0  ...   175.1   384.0  367.849057   352.0   55.72   57.57   42.08   
61  436.0  ...   115.9   384.0  370.000000   354.0    0.00    0.00    0.00   
64  437.0  ...   147.1   384.0  367.943396   352.0    0.00    0.00    0.00   
65  441.0  ...   118.9   383.0  368.056604   352.0   51.55   55.55   39.85   
66  446.0  ...   177.0   384.0  369.111111   353.0   51.37   55.70   52.49   

    X_2869  X_2870  X_2871  
7    57.99   63.16     1.0  
8    47.94   60.72     1.0  
14   48.62   63.18     1.0  
35   56.16   64.25     1.0  
41   55.19   67.17     1.0  
42   53.75   62.58     1.0  
52   57.75   63.94     1.0  
53   57.22   63.33     1.0  
54   55.19   66.06     1.0  
61    0.00    0.00     1.0  
64    0.00    0.00     1.0  
65   47.82   61.59     1.0  
66   48.34   62.12     1.0  

[13 rows x 1969 columns]

In [106]:
TT050304 = TT050304.fillna(T050304.mean())
TT050307 = TT050307.fillna(T050307.mean())
TT010305 = TT010305.fillna(T010305.mean())
TT010306 = TT010306.fillna(T010306.mean())
TT100304 = TT100304.fillna(T100304.mean())
TT100306 = TT100306.fillna(T100306.mean())
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7              1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8              1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14             1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35             1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41             1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42             1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52             1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53             1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54             1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61             1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64             1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65             1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66             1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
7   354.0  ...  369.462963   354.0  57.740000  52.510000  54.450000   
8   355.0  ...  370.259259   353.0  53.180000  56.020000  41.790000   
14   60.0  ...  369.377359   353.0  49.770000  54.930000  49.850000   
35  249.0  ...  369.660377   352.0  55.220000  58.140000  48.930000   
41  293.0  ...  368.018519   352.0  49.670000  45.000000  49.810000   
42  293.0  ...  368.452830   353.0  51.300000  47.660000  60.000000   
52  330.0  ...  368.320755   353.0  54.060000  51.180000  52.170000   
53  330.0  ...  361.226415   342.0  54.040000  51.250000  54.980000   
54  330.0  ...  367.849057   352.0  55.720000  57.570000  42.080000   
61  436.0  ...  370.000000   354.0  50.921667  53.674487  48.381103   
64  437.0  ...  367.943396   352.0  50.921667  53.674487  48.381103   
65  441.0  ...  368.056604   352.0  51.550000  55.550000  39.850000   
66  446.0  ...  369.111111   353.0  51.370000  55.700000  52.490000   

       X_2869     X_2870  X_2871  HOUR  DAY_OF_WEEK  
7   57.990000  63.160000     1.0    12            6  
8   47.940000  60.720000     1.0    12            6  
14  48.620000  63.180000     1.0     6            6  
35  56.160000  64.250000     1.0     3            7  
41  55.190000  67.170000     1.0    23            1  
42  53.750000  62.580000     1.0    23            1  
52  57.750000  63.940000     1.0    17            3  
53  57.220000  63.330000     1.0    17            3  
54  55.190000  66.060000     1.0    18            3  
61  51.671321  67.064269     1.0    21            7  
64  51.671321  67.064269     1.0     0            1  
65  47.820000  61.590000     1.0     3            1  
66  48.340000  62.120000     1.0     8            1  

[13 rows x 1971 columns]

In [249]:
zero_one = (train_data[train_data['Y_Class'] == 1]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 0]['Y_Quality'].max())/2
one_two = (train_data[train_data['Y_Class'] == 2]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 1]['Y_Quality'].max())/2
print(zero_one, one_two)

0.5250761905000001 0.5348968255


# Test Model

In [117]:
TT050304_prediction = predict_model(T050304_final_regression_model, data=TT050304)
TT050307_prediction = predict_model(T050307_final_regression_model, data=TT050307)
TT010305_prediction = predict_model(T010305_final_regression_model, data=TT010305)
TT010306_prediction = predict_model(T010306_final_regression_model, data=TT010306)
TT100304_prediction = predict_model(T100304_final_regression_model, data=TT100304)
TT100306_prediction = predict_model(T100306_final_regression_model, data=TT100306)

In [118]:
TT050304_y_class = pd.DataFrame(TT050304, columns = ['Y_Class'])
TT050304_idx = TT050304_y_class.index
TT050304_y_class = TT050304_y_class.reset_index()
TT050304_prediction = pd.concat([TT050304_prediction, TT050304_y_class], axis = 1)
TT050304_prediction = TT050304_prediction.set_index('index')
TT050304_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [119]:
TT050307_y_class = pd.DataFrame(TT050307, columns = ['Y_Class'])
TT050307_idx = TT050307_y_class.index
TT050307_y_class = TT050307_y_class.reset_index()
TT050307_prediction = pd.concat([TT050307_prediction, TT050307_y_class], axis = 1)
TT050307_prediction = TT050307_prediction.set_index('index')
TT050307_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [120]:
TT010305_y_class = pd.DataFrame(TT010305, columns = ['Y_Class'])
TT010305_idx = TT010305_y_class.index
TT010305_y_class = TT010305_y_class.reset_index()
TT010305_prediction = pd.concat([TT010305_prediction, TT010305_y_class], axis = 1)
TT010305_prediction = TT010305_prediction.set_index('index')
TT010305_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [121]:
TT010306_y_class = pd.DataFrame(TT010306, columns = ['Y_Class'])
TT010306_idx = TT010306_y_class.index
TT010306_y_class = TT010306_y_class.reset_index()
TT010306_prediction = pd.concat([TT010306_prediction, TT010306_y_class], axis = 1)
TT010306_prediction = TT010306_prediction.set_index('index')
TT010306_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [122]:
TT100304_y_class = pd.DataFrame(TT100304, columns = ['Y_Class'])
TT100304_idx = TT100304_y_class.index
TT100304_y_class = TT100304_y_class.reset_index()
TT100304_prediction = pd.concat([TT100304_prediction, TT100304_y_class], axis = 1)
TT100304_prediction = TT100304_prediction.set_index('index')
TT100304_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [123]:
TT100306_y_class = pd.DataFrame(TT100306, columns = ['Y_Class'])
TT100306_idx = TT100306_y_class.index
TT100306_y_class = TT100306_y_class.reset_index()
TT100306_prediction = pd.concat([TT100306_prediction, TT100306_y_class], axis = 1)
TT100306_prediction = TT100306_prediction.set_index('index')
TT100306_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [124]:
TT050304_prediction['Y_Class'] = 22

TT100304_idx = TT050304_prediction.index
for i in range (len(TT050304_prediction)) :
    if (TT050304_prediction.iloc[i]['prediction_label'] <= (0.525045+0.525095)/2) :
        TT050304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 0
    elif ((0.525045+0.525095)/2 < TT050304_prediction.iloc[i]['prediction_label']) and (TT050304_prediction.iloc[i]['prediction_label'] < (0.534054+0.535405)/2) :
        TT050304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 1
    elif ((0.534054+0.535405)/2 <= TT050304_prediction.iloc[i]['prediction_label']) :
        TT050304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 2
TT050304_prediction['Y_Class'].unique()

array([1, 0], dtype=int64)

In [125]:
TT050307_prediction['Y_Class'] = 22

TT050307_idx = TT050307_prediction.index
for i in range (len(TT050307_prediction)) :
    if (TT050307_prediction.iloc[i]['prediction_label'] <= (0.524781+0.525086)/2) :
        TT050307_prediction.loc[TT050307_idx[i], 'Y_Class'] = 0
    elif ((0.524781+0.525086)/2 < TT050307_prediction.iloc[i]['prediction_label']) and (TT050307_prediction.iloc[i]['prediction_label'] < (0.534843+0.537325)/2) :
        TT050307_prediction.loc[TT050307_idx[i], 'Y_Class'] = 1
    elif ((0.534843+0.537325)/2 <= TT050307_prediction.iloc[i]['prediction_label']) :
        TT050307_prediction.loc[TT050307_idx[i], 'Y_Class'] = 2
TT050307_prediction['Y_Class'].unique()

array([1], dtype=int64)

In [126]:
TT010305_prediction['Y_Class'] = 22

TT010305_idx = TT010305_prediction.index
for i in range (len(TT010305_prediction)) :
    if (TT010305_prediction.iloc[i]['prediction_label'] <= (0.524808 +0.526241)/2) :
        TT010305_prediction.loc[TT010305_idx[i], 'Y_Class'] = 0
    elif ((0.524808 +0.526241)/2 < TT010305_prediction.iloc[i]['prediction_label']) and (TT010305_prediction.iloc[i]['prediction_label'] < (0.534486+0.535741)/2) :
        TT010305_prediction.loc[TT010305_idx[i], 'Y_Class'] = 1
    elif ((0.534486+0.535741)/2 <= TT010305_prediction.iloc[i]['prediction_label']) :
        TT010305_prediction.loc[TT010305_idx[i], 'Y_Class'] = 2
TT010305_prediction['Y_Class'].unique()

array([0, 1, 2], dtype=int64)

In [127]:
TT010306_prediction['Y_Class'] = 22

TT010306_idx = TT010306_prediction.index
for i in range (len(TT010306_prediction)) :
    if (TT010306_prediction.iloc[i]['prediction_label'] <= (0.524487+0.525221)/2) :
        TT010306_prediction.loc[TT010306_idx[i], 'Y_Class'] = 0
    elif ((0.524487+0.525221)/2 < TT010306_prediction.iloc[i]['prediction_label']) and (TT010306_prediction.iloc[i]['prediction_label'] < (0.534737+0.535279)/2) :
        TT010306_prediction.loc[TT010306_idx[i], 'Y_Class'] = 1
    elif ((0.534737+0.535279)/2 <= TT010306_prediction.iloc[i]['prediction_label']) :
        TT010306_prediction.loc[TT010306_idx[i], 'Y_Class'] = 2
TT010306_prediction['Y_Class'].unique()

array([1, 2, 0], dtype=int64)

In [128]:
TT100304_prediction['Y_Class'] = 22

TT100304_idx = TT100304_prediction.index
for i in range (len(TT100304_prediction)) :
    if (TT100304_prediction.iloc[i]['prediction_label'] <= (0.525035+0.525483)/2) :
        TT100304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 0
    elif ((0.525035+0.525483)/2 < TT100304_prediction.iloc[i]['prediction_label']) and (TT100304_prediction.iloc[i]['prediction_label'] < (0.534837+0.534951)/2) :
        TT100304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 1
    elif ((0.534837+0.534951)/2 <= TT100304_prediction.iloc[i]['prediction_label']) :
        TT100304_prediction.loc[TT100304_idx[i], 'Y_Class'] = 2
TT100304_prediction['Y_Class'].unique()

array([1, 0], dtype=int64)

In [129]:
TT100306_prediction['Y_Class'] = 22

TT100306_idx = TT100306_prediction.index
for i in range (len(TT100306_prediction)) :
    if (TT100306_prediction.iloc[i]['prediction_label'] <= (0.525067 +0.525213 )/2) :
        TT100306_prediction.loc[TT100306_idx[i], 'Y_Class'] = 0
    elif ((0.525067 +0.525213 )/2 < TT100306_prediction.iloc[i]['prediction_label']) and (TT100306_prediction.iloc[i]['prediction_label'] < (0.534737+0.534951 )/2) :
        TT100306_prediction.loc[TT100306_idx[i], 'Y_Class'] = 1
    elif ((0.534737+0.534951 )/2 <= TT100306_prediction.iloc[i]['prediction_label']) :
        TT100306_prediction.loc[TT100306_idx[i], 'Y_Class'] = 2
TT100306_prediction['Y_Class'].unique()

array([1, 2], dtype=int64)

In [130]:
final_test = pd.concat([TT050304_prediction, TT050307_prediction, TT010305_prediction, TT010306_prediction, TT100304_prediction, TT100306_prediction])
final_test

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  \
index                                                                      
7                 1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0   
8                 1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0   
14                1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   
35                1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0   
41                1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0   
...             ...      ...      ...    ...    ...    ...    ...    ...   
301               2      NaN      NaN    NaN    NaN    NaN    NaN    NaN   
305               2      NaN      NaN    NaN    NaN    NaN    NaN    NaN   
307               2      NaN      NaN    NaN    NaN    NaN    NaN    NaN   
308               2      NaN      NaN    NaN    NaN    NaN    NaN    NaN   
309               2      NaN      NaN    NaN    NaN    NaN    NaN    NaN   

       X_137  X_138  ...  X_930  X_931      X_932  X_933  X_93  X_94  X_95  \
index                ...                                                     
7      354.0  354.0  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
8      354.0  355.0  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
14      60.0   60.0  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
35     249.0  249.0  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
41     293.0  293.0  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
...      ...    ...  ...    ...    ...        ...    ...   ...   ...   ...   
301      NaN    NaN  ...  298.0   13.6  13.380645   13.2  0.19  0.19  0.19   
305      NaN    NaN  ...  294.0   13.6  13.341935   13.2  0.19  0.19  0.19   
307      NaN    NaN  ...  289.0   13.6  13.361290   13.2  0.19  0.19  0.19   
308      NaN    NaN  ...  290.0   13.6  13.335484   13.2  0.19  0.19  0.19   
309      NaN    NaN  ...  289.0   13.6  13.343333   13.2  0.19  0.19  0.19   

       X_104    X_126    X_127  
index                           
7        NaN      NaN      NaN  
8        NaN      NaN      NaN  
14       NaN      NaN      NaN  
35       NaN      NaN      NaN  
41       NaN      NaN      NaN  
...      ...      ...      ...  
301     28.0  34979.0  34979.0  
305     28.0  35871.0  35871.0  
307     28.0  36150.0  36150.0  
308     28.0  36399.0  36399.0  
309     28.0  36414.0  36414.0  

[310 rows x 2796 columns]

In [131]:
final_test = final_test.sort_index(ascending=True)
final_test['Y_Class']

index
0      1
1      1
2      1
3      0
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: Y_Class, Length: 310, dtype: int64

In [135]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['Y_Class']
display(sample_submission.head())
sample_submission.to_csv('line6regclass0_andsep_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        0
4   TEST_004        1

In [133]:
final_test['Y_Class'].value_counts()

1    267
0     29
2     14
Name: Y_Class, dtype: int64

In [134]:
np.array(final_test['Y_Class'])

array([1, 1, 1, 0, 1, 1, 1, 1, 0, 2, 0, 1, 2, 1, 1, 1, 1, 0, 1, 1, 0, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 0, 1, 0, 2, 1, 1, 1, 0, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 2, 0, 2,
       0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 2, 2, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 2, 1, 1, 1, 1, 0, 0, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,